In [1]:
import requests
import json
from pprint import pprint
from datetime import datetime,time
import time as sleep
import sys
from configparser import ConfigParser
from requests.auth import HTTPBasicAuth
from urllib.parse import quote_plus

In [2]:
configur = ConfigParser() 
configur.read('config.ini')

# Telegram setup
bot_token = configur.get('telegram', 'bot_token')

# Telegram setup Pune
# Pune District
chatIdPuneDistrict = configur.get('telegram', 'PuneDistrict')

# Telegram setup Nashik Group
# Nashik District
chatIdNskDistrict = configur.get('telegram', 'NashikDistrict')

#District data
state = configur.get('data', 'state')
districts = json.loads(configur.get('data', 'districts'))
global hitCount
hitCount = 0

In [3]:
def sendMsg(place,name,address,pin,vaccine,v_count,age,fee):
    if(place == 389): #NashikDistrictCode
        bot_chatID = chatIdNskDistrict
    elif(place == 363): #PuneDistrictCode
        bot_chatID = chatIdPuneDistrict

    msg = "ALERT! Slot available!\nName: " + str(name) + "\nAddress : " + str(address) + "\nPincode : " + str(pin) + "\nVaccine : " + str(vaccine) + " : " + str(fee) + "\nAge : " + str(age) + "+" + "\nTotal Slots : " + str(v_count)
    msg = format(quote_plus(msg))
    send_text = 'https://api.telegram.org/bot' + bot_token + '/sendMessage?chat_id=' + bot_chatID + '&text=' + msg
#     print(send_text)
    response = requests.get(send_text)
    return response.json()

In [4]:
def getStateId(name):
    global hitCount
    s_id = 21
    try:
        url = "https://cdn-api.co-vin.in/api/v2/admin/location/states"
        headers = {'User-Agent': "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/90.0.4430.93 Safari/537.36"}
        response = requests.get(url, headers=headers)
#         print(response)
        hitCount += 1
        response = response.content.decode()
        jsonData = json.loads(response)
#         print(jsonData)
        for state in jsonData['states']:
            if (state['state_name'].upper() == name.upper()):
                s_id = state['state_id']
    except:
        print(sys.exc_info())
    return s_id

In [5]:
def getDistrictId(s_name,d_name):
    global hitCount
    s_id = getStateId(s_name);
    d_id = [];
    
    try:
        url = "https://cdn-api.co-vin.in/api/v2/admin/location/districts/"+str(s_id)
        headers = {'User-Agent': "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/90.0.4430.93 Safari/537.36"}
        response = requests.get(url, headers=headers)
        hitCount += 1
        response = response.content.decode()
        jsonData = json.loads(response)
        for d in d_name:
            for district in jsonData['districts']:
                if (district['district_name'].upper() == d.upper()):
                    d_id.append(district['district_id'])
    except:
        print(sys.exc_info())
    return d_id


In [10]:
def checkSlotsByDistrict(s_name, d_name):
    global hitCount
    ids = getDistrictId(s_name, d_name)
    for d_id in ids: 
        sleep.sleep(1)
        try:
            today = datetime.now().date()
#             today = datetime.now().date() + timedelta(1)
#             print(today)
            today = today.strftime('%d-%m-%Y');
            url = "https://cdn-api.co-vin.in/api/v2/appointment/sessions/calendarByDistrict?district_id="+str(d_id)+"&date="+str(today)

            headers = {'User-Agent': "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/90.0.4430.93 Safari/537.36"}
            response = requests.get(url, headers=headers)
            hitCount += 1
            print(response)
            response = response.content.decode()
            jsonData = json.loads(response)
            jsonData = jsonData['centers']

            for center in jsonData:
                centerName = center['name']
                address = center['address']
                pin = center['pincode']
                fee = center['fee_type']
                for sessions in center['sessions']:
                    if (today == sessions['date']):
                        if(sessions['available_capacity'] > 0):
                            if center['center_id'] in entry_list:
                                pass
                            else:
                                print("Slot Available!")
                                print(center['center_id'],centerName,address,sessions['vaccine'],sessions['available_capacity'],sessions['min_age_limit'],fee)
                                entry_list.append(center['center_id'])
                                sendMsg(d_id,centerName,address,pin,sessions['vaccine'],sessions['available_capacity'],sessions['min_age_limit'],fee)
                        print(center['center_id'],centerName,address,sessions['vaccine'],sessions['available_capacity'],sessions['min_age_limit'],fee)
        except:
            pass

In [ ]:
done = False
i = 1
entry_list = []
while not done:
    
    hitCount = 0
    print(hitCount)
    now = datetime.now().time()
    
#     if(now > time(7,00) and now < time(23,00)):
        
    #By District
    checkSlotsByDistrict(state,districts)


    print("loop : " + str(i) + " Time : " + str(now))
    i += 1
    print(entry_list)
    sleep.sleep(5)
    if(i%120 == 0):
        #list cleared
        entry_list = []
#     else:
#         done = True
    print(hitCount)

0
<Response [200]>
629089 Sangavi Hosp P A Holkar School Near Gajanan Bus StopMain Road Shri Krishna Sty Old Sangvi Pimpri-Chinchwad Pune Maharashtra 411027 COVISHIELD 0 45 Free
563789 YCM Hospital Utarayana Hotel Rd Near Yashwantrao Chavan Memorial Hospital Yayati Housing Society Sant Tukaram Nagar Pimpri Colony Pune Maharashtra 411018 COVISHIELD 0 45 Free
631789 Murlidhar Laigude Rajyog Society Vadgaon KhurdNanded FataPandurang Industrial Area Rajyog RoadDhayari Pune COVAXIN 0 45 Free
605451 BabaSaheb Ambedkar Dias Plot Dias Plot Pune COVAXIN 0 45 Free
605443 Bhangire Hospital Mohammadwadi Mohammadwadi PMC Pune COVAXIN 0 45 Free
607374 Naidu Hospital Covaxin Near RTO Office Pune COVAXIN 0 45 Free
699755 SANT RAMDAS SCHOOL (KANNAD) PANDAV NAGARWADARWADI COVAXIN 0 45 Free
561288 Jijamata Hospital UHC 1 Near Gurudwara Pimpri Pune COVISHIELD 0 45 Free
631535 Covaxin Rajiv Gandhi Hospit Yerwada Pune COVAXIN 0 45 Free
605508 Malti Kachi Hospital Sukrawar Peth COVAXIN 0 45 Free
607439 Vilas

<Response [200]>
612815 Jaydar PHC At Post Jaydar COVISHIELD 0 45 Free
613720 Tirhal PHC At Post Tirahl COVISHIELD 0 45 Free
607067 1 Kanashi At Post Kanashi COVISHIELD 0 45 Free
603679 PHC Nanduri At Post Nanduri Tal Kalwan COVISHIELD 0 45 Free
loop : 5 Time : 14:44:09.229480
[]
4
0
<Response [200]>
629089 Sangavi Hosp P A Holkar School Near Gajanan Bus StopMain Road Shri Krishna Sty Old Sangvi Pimpri-Chinchwad Pune Maharashtra 411027 COVISHIELD 0 45 Free
563789 YCM Hospital Utarayana Hotel Rd Near Yashwantrao Chavan Memorial Hospital Yayati Housing Society Sant Tukaram Nagar Pimpri Colony Pune Maharashtra 411018 COVISHIELD 0 45 Free
631789 Murlidhar Laigude Rajyog Society Vadgaon KhurdNanded FataPandurang Industrial Area Rajyog RoadDhayari Pune COVAXIN 0 45 Free
605451 BabaSaheb Ambedkar Dias Plot Dias Plot Pune COVAXIN 0 45 Free
605443 Bhangire Hospital Mohammadwadi Mohammadwadi PMC Pune COVAXIN 0 45 Free
607374 Naidu Hospital Covaxin Near RTO Office Pune COVAXIN 0 45 Free
699755 SA

<Response [200]>
612815 Jaydar PHC At Post Jaydar COVISHIELD 0 45 Free
613720 Tirhal PHC At Post Tirahl COVISHIELD 0 45 Free
607067 1 Kanashi At Post Kanashi COVISHIELD 0 45 Free
603679 PHC Nanduri At Post Nanduri Tal Kalwan COVISHIELD 0 45 Free
loop : 9 Time : 14:44:51.107700
[]
4
0
<Response [401]>
<Response [200]>
612815 Jaydar PHC At Post Jaydar COVISHIELD 0 45 Free
613720 Tirhal PHC At Post Tirahl COVISHIELD 0 45 Free
607067 1 Kanashi At Post Kanashi COVISHIELD 0 45 Free
603679 PHC Nanduri At Post Nanduri Tal Kalwan COVISHIELD 0 45 Free
loop : 10 Time : 14:44:58.838040
[]
4
0
<Response [200]>
629089 Sangavi Hosp P A Holkar School Near Gajanan Bus StopMain Road Shri Krishna Sty Old Sangvi Pimpri-Chinchwad Pune Maharashtra 411027 COVISHIELD 0 45 Free
563789 YCM Hospital Utarayana Hotel Rd Near Yashwantrao Chavan Memorial Hospital Yayati Housing Society Sant Tukaram Nagar Pimpri Colony Pune Maharashtra 411018 COVISHIELD 0 45 Free
631789 Murlidhar Laigude Rajyog Society Vadgaon KhurdN

<Response [401]>
loop : 14 Time : 14:45:29.155651
[]
4
0
<Response [200]>
629089 Sangavi Hosp P A Holkar School Near Gajanan Bus StopMain Road Shri Krishna Sty Old Sangvi Pimpri-Chinchwad Pune Maharashtra 411027 COVISHIELD 0 45 Free
563789 YCM Hospital Utarayana Hotel Rd Near Yashwantrao Chavan Memorial Hospital Yayati Housing Society Sant Tukaram Nagar Pimpri Colony Pune Maharashtra 411018 COVISHIELD 0 45 Free
631789 Murlidhar Laigude Rajyog Society Vadgaon KhurdNanded FataPandurang Industrial Area Rajyog RoadDhayari Pune COVAXIN 0 45 Free
605451 BabaSaheb Ambedkar Dias Plot Dias Plot Pune COVAXIN 0 45 Free
605443 Bhangire Hospital Mohammadwadi Mohammadwadi PMC Pune COVAXIN 0 45 Free
607374 Naidu Hospital Covaxin Near RTO Office Pune COVAXIN 0 45 Free
699755 SANT RAMDAS SCHOOL (KANNAD) PANDAV NAGARWADARWADI COVAXIN 0 45 Free
561288 Jijamata Hospital UHC 1 Near Gurudwara Pimpri Pune COVISHIELD 0 45 Free
631535 Covaxin Rajiv Gandhi Hospit Yerwada Pune COVAXIN 0 45 Free
605508 Malti Kach

<Response [200]>
612815 Jaydar PHC At Post Jaydar COVISHIELD 0 45 Free
613720 Tirhal PHC At Post Tirahl COVISHIELD 0 45 Free
607067 1 Kanashi At Post Kanashi COVISHIELD 0 45 Free
603679 PHC Nanduri At Post Nanduri Tal Kalwan COVISHIELD 0 45 Free
loop : 18 Time : 14:45:59.443782
[]
4
0
<Response [200]>
629089 Sangavi Hosp P A Holkar School Near Gajanan Bus StopMain Road Shri Krishna Sty Old Sangvi Pimpri-Chinchwad Pune Maharashtra 411027 COVISHIELD 0 45 Free
563789 YCM Hospital Utarayana Hotel Rd Near Yashwantrao Chavan Memorial Hospital Yayati Housing Society Sant Tukaram Nagar Pimpri Colony Pune Maharashtra 411018 COVISHIELD 0 45 Free
631789 Murlidhar Laigude Rajyog Society Vadgaon KhurdNanded FataPandurang Industrial Area Rajyog RoadDhayari Pune COVAXIN 0 45 Free
605451 BabaSaheb Ambedkar Dias Plot Dias Plot Pune COVAXIN 0 45 Free
605443 Bhangire Hospital Mohammadwadi Mohammadwadi PMC Pune COVAXIN 0 45 Free
607374 Naidu Hospital Covaxin Near RTO Office Pune COVAXIN 0 45 Free
699755 S

...

4
0
<Response [200]>
6631 Bhose Sc 1 Bhose,khed,pune COVAXIN 0 45 Free
592517 Primary Health Centre Karla Primary Health Centre Karla COVISHIELD 0 45 Free
13274 District Hospital Aundh District Hospital Aundh Sangavi Phata COVAXIN 0 45 Free
619964 MH KIRKEE ONLY ARMY AND ECHS Militery Hospital Kharkee COVISHIELD 1 45 Free
619533 CH (SC) PUNE FOR ARMED FORCES Command Hospital Pune COVISHIELD 0 45 Free
<Response [200]>
630681 PHC Palkhed Near Bajartal Palkhed (M) COVISHIELD 0 45 Free
589468 Karanjali Phc Karanjali COVISHIELD 10 45 Free
698201 Yeola RH 1 Yeola Rural Hospital Yeola COVISHIELD 0 45 Free
591173 PhcPatoda01 At Post Patoda COVISHIELD 0 45 Free
606128 2 Wadiya Hospital Wadiya Hospital Near MMC Malegaon COVISHIELD 0 45 Free
57954 Borgaon PHC AT POST BORGAON NEAR NDCC BANK BORGAON COVISHIELD 0 45 Free
571132 Indira Gandhi Hospital 1 Panchwati Karanja COVAXIN 0 45 Free
578008 E.S.I.S HOSPITAL SATPUR COVAXIN 0 45 Free
572306 DEOLALI CANT DEOLALI COVAXIN 0 45 Free
48455 Vaitarana PH

4
0
<Response [200]>
6631 Bhose Sc 1 Bhose,khed,pune COVAXIN 0 45 Free
592517 Primary Health Centre Karla Primary Health Centre Karla COVISHIELD 0 45 Free
13274 District Hospital Aundh District Hospital Aundh Sangavi Phata COVAXIN 0 45 Free
619964 MH KIRKEE ONLY ARMY AND ECHS Militery Hospital Kharkee COVISHIELD 1 45 Free
619533 CH (SC) PUNE FOR ARMED FORCES Command Hospital Pune COVISHIELD 0 45 Free
<Response [200]>
630681 PHC Palkhed Near Bajartal Palkhed (M) COVISHIELD 0 45 Free
589468 Karanjali Phc Karanjali COVISHIELD 10 45 Free
698201 Yeola RH 1 Yeola Rural Hospital Yeola COVISHIELD 0 45 Free
591173 PhcPatoda01 At Post Patoda COVISHIELD 0 45 Free
606128 2 Wadiya Hospital Wadiya Hospital Near MMC Malegaon COVISHIELD 0 45 Free
57954 Borgaon PHC AT POST BORGAON NEAR NDCC BANK BORGAON COVISHIELD 0 45 Free
571132 Indira Gandhi Hospital 1 Panchwati Karanja COVAXIN 0 45 Free
578008 E.S.I.S HOSPITAL SATPUR COVAXIN 0 45 Free
572306 DEOLALI CANT DEOLALI COVAXIN 0 45 Free
48455 Vaitarana PH

4
0
<Response [200]>
6631 Bhose Sc 1 Bhose,khed,pune COVAXIN 0 45 Free
592517 Primary Health Centre Karla Primary Health Centre Karla COVISHIELD 0 45 Free
13274 District Hospital Aundh District Hospital Aundh Sangavi Phata COVAXIN 0 45 Free
619964 MH KIRKEE ONLY ARMY AND ECHS Militery Hospital Kharkee COVISHIELD 1 45 Free
619533 CH (SC) PUNE FOR ARMED FORCES Command Hospital Pune COVISHIELD 0 45 Free
<Response [200]>
630681 PHC Palkhed Near Bajartal Palkhed (M) COVISHIELD 0 45 Free
589468 Karanjali Phc Karanjali COVISHIELD 10 45 Free
698201 Yeola RH 1 Yeola Rural Hospital Yeola COVISHIELD 0 45 Free
591173 PhcPatoda01 At Post Patoda COVISHIELD 0 45 Free
606128 2 Wadiya Hospital Wadiya Hospital Near MMC Malegaon COVISHIELD 0 45 Free
57954 Borgaon PHC AT POST BORGAON NEAR NDCC BANK BORGAON COVISHIELD 0 45 Free
571132 Indira Gandhi Hospital 1 Panchwati Karanja COVAXIN 0 45 Free
578008 E.S.I.S HOSPITAL SATPUR COVAXIN 0 45 Free
572306 DEOLALI CANT DEOLALI COVAXIN 0 45 Free
48455 Vaitarana PH

0
0
<Response [200]>
6631 Bhose Sc 1 Bhose,khed,pune COVAXIN 0 45 Free
7587 Walha PHC Walha PHC Taluka Purandar 412305 COVISHIELD 0 45 Free
592517 Primary Health Centre Karla Primary Health Centre Karla COVISHIELD 0 45 Free
13274 District Hospital Aundh District Hospital Aundh Sangavi Phata COVAXIN 0 45 Free
619533 CH (SC) PUNE FOR ARMED FORCES Command Hospital Pune COVISHIELD 0 45 Free
619964 MH KIRKEE ONLY ARMY AND ECHS Militery Hospital Kharkee COVISHIELD 2 45 Free
643947 Pune Cantonment Hospital Sardar Vallabhbhai Patel Cantonment General Hospital Pune COVISHIELD 0 45 Free
<Response [200]>
617449 Dapur Phc At Post Dapur tal -Sinner COVISHIELD 0 45 Free
630681 PHC Palkhed Near Bajartal Palkhed (M) COVISHIELD 0 45 Free
589468 Karanjali Phc Karanjali COVISHIELD 10 45 Free
698201 Yeola RH 1 Yeola Rural Hospital Yeola COVISHIELD 0 45 Free
684739 SC Kharwal Virnagar At Virnagar Post Kharwal Trimbak COVISHIELD 0 45 Free
591173 PhcPatoda01 At Post Patoda COVISHIELD 0 45 Free
606128 2 Wadiy

4
0
<Response [200]>
6631 Bhose Sc 1 Bhose,khed,pune COVAXIN 0 45 Free
7587 Walha PHC Walha PHC Taluka Purandar 412305 COVISHIELD 0 45 Free
592517 Primary Health Centre Karla Primary Health Centre Karla COVISHIELD 0 45 Free
13274 District Hospital Aundh District Hospital Aundh Sangavi Phata COVAXIN 0 45 Free
619533 CH (SC) PUNE FOR ARMED FORCES Command Hospital Pune COVISHIELD 0 45 Free
619964 MH KIRKEE ONLY ARMY AND ECHS Militery Hospital Kharkee COVISHIELD 2 45 Free
643947 Pune Cantonment Hospital Sardar Vallabhbhai Patel Cantonment General Hospital Pune COVISHIELD 0 45 Free
